In [1]:
from huggingface_hub import notebook_login

notebook_login()

In [2]:
import os

os.environ['HF_HOME'] = 'E:/Models/hf_cache'
os.environ['HUGGINGFACE_HUB_CACHE'] = 'E:/Models/hf_cache'

In [3]:
import pandas as pd

aqua_train_path = 'E:/Data/AQuA Dataset/train.json'

df = pd.read_json(aqua_train_path, lines = True)
df = df.head(5000)

In [4]:
df.shape

(5000, 4)

In [5]:
df.head()

question  \
0  Two friends plan to walk along a 43-km trail, ...   
1  In the coordinate plane, points (x, 1) and (5,...   
2  For all numbers p and q, the operation @ is de...   
3  Carl is facing very difficult financial times ...   
4  The speed at which a man can row a boat in sti...   

                                             options  \
0                 [A)21, B)21.5, C)22, D)22.5, E)23]   
1  [A)4 and 1, B)1 and 5, C)5 and 1, D)3 and 5, E...   
2  [A)II, B)I and II, C)I and III, D)II and III, ...   
3     [A)$1600, B)$2000, C)$2150, D)$2500, E)$12000]   
4  [A)18 seconds, B)27 seconds, C)26 seconds, D)1...   

                                           rationale correct  
0  If Q complete x kilometers, then P completes 1...       E  
1  Line k passes through the origin and has slope...       C  
2  p@q = p^2 - pq=p(p-q).... so p@q will be zero ...       B  
3  Usually, you are given the annual rate of inte...       A  
4  Speed of the boat downstream = 25 +11\n= 36 km...       E

In [6]:
from sklearn.metrics import accuracy_score
def solve_rate(true_labels, predictions):
    """Calculates accuracy, correctly handling None as incorrect."""
    if not true_labels:
        return 0.0
    correct_count = sum(1 for p, t in zip(predictions, true_labels) if p == t)
    return correct_count / len(true_labels)

In [7]:
def create_chat_prompt(question, options):
    options_str = " ".join(options)
    messages = [
        {"role": "user", "content": "Q: John found that the average of 15 numbers is 40. If 10 is added to each number then the mean of the numbers is?\nAnswer Choices: (a) 50 (b) 45 (c) 65 (d) 78 (e) 64\nPlease show your reasoning step by step."},
        {"role": "assistant", "content": "A: If 10 is added to each number, then the mean of the numbers also increases by 10. So the new mean would be 50. The answer is (a)."},
        {"role": "user", "content": "Q: If a / b = 3/4 and 8a + 5b = 22, then find the value of a.\nAnswer Choices: (a) 1/2 (b) 3/2 (c) 5/2 (d) 4/2 (e) 7/2\nPlease show your reasoning step by step."},
        {"role": "assistant", "content": "A: If a / b = 3/4, then b = 4a / 3. So 8a + 5(4a / 3) = 22. This simplifies to 8a + 20a / 3 = 22, which means 44a / 3 = 22. So a = 3/2. The answer is (b)."},
        {"role": "user", "content": "Q: A person is traveling at 20 km/hr and reached his destiny in 2.5 hr then find the distance?\nAnswer Choices: (a) 53 km (b) 55 km (c) 52 km (d) 60 km (e) 50 km\nPlease show your reasoning step by step."},
        {"role": "assistant", "content": "A: The distance the person traveled would have been 20 km/hr * 2.5 hrs = 50 km. The answer is (e)."},
        {
            "role": "user",
            "content": f"Q: {question}\nAnswer Choices: {options_str}\nPlease show your reasoning step by step. Your final answer must be in the format \"The answer is (X).\""
        }
    ]
    return messages

In [8]:
import re
def extract_answer(text):
    patterns = [
        r"[Tt]he answer is:?\s*\(([a-eA-E])\)",  # Standard format
        r"[Aa]nswer:?\s*\(([a-eA-E])\)",          # Alternative format
        r"\(([a-eA-E])\)[.,;]?\s*$",              # Answer at end of text
        r"[Tt]herefore,?\s*(?:the answer is)?\s*\(([a-eA-E])\)",  # With "therefore"
    ]
    
    for pattern in patterns:
        match = re.search(pattern, text, re.IGNORECASE)
        if match:
            return match.group(1).upper()
    
    # Last resort: find any isolated letter in parentheses near the end
    matches = re.findall(r"\(([a-eA-E])\)", text)
    if matches:
        return matches[-1].upper()  # Return the last match
    
    return None


In [9]:
example_text = "The answer is (b)."
print(extract_answer(example_text))

B


In [10]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

model_name = "google/gemma-2-2b-it" 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using model: {model_name} on device: {device}")

tokenizer = AutoTokenizer.from_pretrained(model_name)
if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token

nf4_config = BitsAndBytesConfig(
   load_in_4bit=True,
   bnb_4bit_quant_type="nf4",
   bnb_4bit_use_double_quant=True,
   bnb_4bit_compute_dtype=torch.bfloat16
)

model = AutoModelForCausalLM.from_pretrained(
    model_name,
    quantization_config=nf4_config,
    device_map="auto"
)
print(f"Model '{model_name}' loaded successfully.")


Using model: google/gemma-2-2b-it on device: cuda


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Model 'google/gemma-2-2b-it' loaded successfully.


In [11]:
predictions = []
true_labels = []
output_file_path = "aqua_results_gemma.txt"

for i, (index, row) in enumerate(df.iterrows()):
        question = row['question']
        options = row['options']
        correct_label = row['correct']

        messages = create_chat_prompt(question, options)
        prompt_string = tokenizer.apply_chat_template(
            messages,
            tokenize=False,
            add_generation_prompt=True
        )
        
        inputs = tokenizer(prompt_string, return_tensors="pt").to(device)
        
        outputs = model.generate(
            **inputs,
            max_new_tokens=512,
            do_sample=False,
            pad_token_id=tokenizer.eos_token_id
        )

        full_response = tokenizer.decode(outputs[0], skip_special_tokens=True)
        rationale = full_response[len(prompt_string):].strip()
        predicted_answer = extract_answer(rationale)
        
        print(f"Question: {question}\n")
        print(f"Rationale: {rationale}\n")
        print(f"Answer: {predicted_answer}\n")
        print("-" * 50 + "\n\n")

        print(f"({i+1}/{len(df)}) Predicted: {predicted_answer} | Correct: {correct_label}")
        print("-" * 50 + "\n\n")

        predictions.append(predicted_answer)
        true_labels.append(correct_label)
    

print(f"\nEvaluation complete. All outputs saved to '{output_file_path}'")


Question: Two friends plan to walk along a 43-km trail, starting at opposite ends of the trail at the same time. If Friend P's rate is 15% faster than Friend Q's, how many kilometers will Friend P have walked when they pass each other?

Rationale: Friend Q's speed (in km/hr).
* Friend P's speed is 1.15x km/hr.

**3.  Set up the Equation:**

* The total distance is 43 km.
* Time taken by Friend Q:  Distance / Speed = 43 / x
* Time taken by Friend P: Distance / Speed = 43 / 1.15x

**4.  Find the Time When They Meet:**

* Since they meet at the same time, the time taken by both is the same.  
*  Let's call this time 't'

**5.  Set up the Equation:**

*  43 / x = t
*  43 / 1.15x = t

**6.  Solve for 't'**

*  We know that the time taken by both is the same. 
*  Therefore, 43 / x = 43 / 1.15x

**7.  Solve for 'x'**

*  Cross-multiply: 43 * 1.15x = 43x
*  Simplify: 49.95x = 43x
*  Solve for x: 6.95x = 0
*  x = 0 km/hr

**8.  Find the Distance Traveled by Friend P:**

*  We know that Friend P

In [12]:
# --- Calculate and Display Final Accuracy ---

if true_labels:
    accuracy = solve_rate(true_labels, predictions)
    print(f"\nFinal Accuracy on {len(true_labels)} samples: {accuracy * 100:.2f}%")
else:
    print("\nNo samples were processed to calculate accuracy.")


Final Accuracy on 5000 samples: 27.72%
